In [1]:
import tensorflow as tf
from tensorflow.examples.tutorials.mnist import input_data

# Read data
mnist = input_data.read_data_sets("MNIST_data/", one_hot=True)

Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use urllib or similar directly.
Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST_data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Instructions for updating:
Please use tf.one_hot on tensors.
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py fr

In [12]:
image_size = 28
labels_size = 10
learning_rate = 0.05
steps_number = 1000
batch_size = 100
print(labels)

Tensor("Placeholder_1:0", shape=(?, 10), dtype=float32)


In [3]:
# Define placeholders
training_data = tf.placeholder(tf.float32, [None, image_size*image_size])
labels = tf.placeholder(tf.float32, [None, labels_size])

In [4]:
# Variables to be tuned
W = tf.Variable(tf.truncated_normal([image_size*image_size, labels_size], stddev=0.1))
b = tf.Variable(tf.constant(0.1, shape=[labels_size]))

# Build the network (only output layer)
output = tf.matmul(training_data, W) + b

Instructions for updating:
Colocations handled automatically by placer.


In [5]:
#Define the loss function
loss = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=labels, logits=output))

# Training step
train_step = tf.train.GradientDescentOptimizer(learning_rate).minimize(loss)

Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.



In [6]:
# Accuracy calculation
correct_prediction = tf.equal(tf.argmax(output, 1), tf.argmax(labels, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

In [7]:
# Run the training
sess = tf.InteractiveSession()
sess.run(tf.global_variables_initializer())

In [9]:
for i in range(steps_number):
  # Get the next batch
  input_batch, labels_batch = mnist.train.next_batch(batch_size)
  feed_dict = {training_data: input_batch, labels: labels_batch}

  # Run the training step
  train_step.run(feed_dict=feed_dict)

  if i%100 == 0:
    train_accuracy = accuracy.eval(feed_dict=feed_dict)
    print("Step %d, training batch accuracy %g %%"%(i, train_accuracy*100))

Step 0, training batch accuracy 92 %
Step 100, training batch accuracy 89 %
Step 200, training batch accuracy 90 %
Step 300, training batch accuracy 92 %
Step 400, training batch accuracy 90 %
Step 500, training batch accuracy 89 %
Step 600, training batch accuracy 89 %
Step 700, training batch accuracy 91 %
Step 800, training batch accuracy 88 %
Step 900, training batch accuracy 89 %


In [10]:
# Evaluate on the test set
test_accuracy = accuracy.eval(feed_dict={training_data: mnist.test.images, labels: mnist.test.labels})
print("Test accuracy: %g %%"%(test_accuracy*100))

Test accuracy: 90.68 %


## Another Example (CNN)

In [13]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

In [14]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [17]:
def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.compat.v1.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.compat.v1.estimator.inputs.numpy_input_fn(
      x={"x": eval_data}, y=eval_labels, num_epochs=1, shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)

if __name__ == "__main__":
  tf.app.run()

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data\train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_expe

INFO:tensorflow:loss = 2.3106732, step = 1
INFO:tensorflow:probabilities = [[0.09949864 0.08619293 0.10752297 0.09429379 0.09343887 0.11662944
  0.10303029 0.09847874 0.1082473  0.09266708]
 [0.09458684 0.10077237 0.10527931 0.09587541 0.09110354 0.10561302
  0.1032583  0.09236629 0.11558776 0.09555715]
 [0.108311   0.09779721 0.10513056 0.09824426 0.09905057 0.10292397
  0.11202328 0.0923868  0.09850953 0.08562274]
 [0.09324574 0.09753666 0.09638198 0.0932385  0.10598853 0.10465132
  0.09874009 0.10317503 0.10762826 0.09941392]
 [0.09192283 0.09478475 0.1044479  0.09397438 0.08928137 0.1028234
  0.11202795 0.09641638 0.11613602 0.09818504]
 [0.09691314 0.09450636 0.10305306 0.10257253 0.09892546 0.09812992
  0.10675327 0.09303737 0.1062837  0.09982524]
 [0.09502087 0.09913032 0.11661992 0.09778381 0.09614325 0.11339457
  0.10050023 0.08931012 0.09978572 0.0923112 ]
 [0.10447437 0.09848724 0.10744597 0.09238012 0.08822918 0.11244898
  0.1041709  0.09136125 0.11367958 0.08732247]
 [0.10

INFO:tensorflow:global_step/sec: 3.27214
INFO:tensorflow:probabilities = [[0.09939234 0.09869302 0.10586181 0.09919842 0.08812331 0.1037468
  0.1011074  0.10796878 0.10864066 0.08726753]
 [0.09890506 0.10454345 0.10857332 0.09420137 0.09454763 0.09603585
  0.10161123 0.09574896 0.11227109 0.09356202]
 [0.09565803 0.09329589 0.0926175  0.09242499 0.10295024 0.10665018
  0.10059949 0.11193392 0.1118845  0.0919853 ]
 [0.09317277 0.10318766 0.10211465 0.10464969 0.09782572 0.10792629
  0.10489141 0.08987755 0.11253326 0.08382093]
 [0.09690337 0.09857072 0.11189575 0.09880644 0.09068722 0.0956957
  0.11858749 0.09416856 0.1016421  0.09304268]
 [0.10781869 0.09897409 0.09662981 0.10478751 0.09520113 0.10404585
  0.10664265 0.09459005 0.10344695 0.08786336]
 [0.10947703 0.09467735 0.10855028 0.09449347 0.10065638 0.10692164
  0.10597385 0.08851229 0.1046683  0.08606941]
 [0.1036043  0.0993633  0.10095327 0.08935411 0.09883533 0.10180047
  0.10368872 0.09207055 0.11466835 0.0956617 ]
 [0.08766

INFO:tensorflow:loss = 2.2933073, step = 101 (30.563 sec)
INFO:tensorflow:probabilities = [[0.10392147 0.10621782 0.1055156  0.09729432 0.08925155 0.10225787
  0.1005367  0.09528086 0.10853435 0.09118941]
 [0.10303544 0.09460407 0.10189497 0.10254088 0.09453586 0.09977671
  0.10950969 0.08885905 0.1094237  0.0958195 ]
 [0.09931713 0.10094661 0.10165297 0.10586326 0.09370762 0.10540284
  0.10100956 0.09638923 0.10070777 0.09500311]
 [0.09856208 0.10030782 0.09959161 0.09393242 0.09892562 0.10012676
  0.09885736 0.09355033 0.10724027 0.10890567]
 [0.10674181 0.10058533 0.10145462 0.09903904 0.08962665 0.10134723
  0.10067079 0.10382085 0.10520363 0.09151004]
 [0.10093775 0.09560539 0.09526857 0.10742657 0.09700517 0.09730692
  0.11007776 0.09968913 0.10581488 0.09086779]
 [0.10286204 0.09337056 0.10437961 0.09707955 0.09131249 0.1001772
  0.10930035 0.08618569 0.11480561 0.10052679]
 [0.09883927 0.10777096 0.10116664 0.08645198 0.09420033 0.10878878
  0.10273021 0.09717754 0.11248752 0.0

INFO:tensorflow:global_step/sec: 2.61382
INFO:tensorflow:probabilities = [[0.09821886 0.10340407 0.09309942 0.09543289 0.09291115 0.10812814
  0.098154   0.09715415 0.1125256  0.10097162]
 [0.10200964 0.0978886  0.09613517 0.09281661 0.10849304 0.10729054
  0.10185728 0.10334989 0.10846482 0.08169437]
 [0.09650347 0.1025996  0.10012626 0.09901635 0.10412621 0.09748781
  0.09691335 0.10094936 0.11052183 0.09175578]
 [0.10539874 0.0908004  0.09538384 0.09832227 0.09418624 0.10949376
  0.11400192 0.08706633 0.11260685 0.0927396 ]
 [0.10974007 0.09758703 0.10735869 0.0923693  0.09214751 0.10180052
  0.09928573 0.09425806 0.10802335 0.09742966]
 [0.10654721 0.09515296 0.11064367 0.10608318 0.08476793 0.09541693
  0.10446077 0.08851136 0.11427301 0.094143  ]
 [0.09378935 0.10396947 0.09538586 0.0995498  0.09215942 0.09157603
  0.10804182 0.09699315 0.12142384 0.0971113 ]
 [0.10199074 0.10661481 0.10231763 0.09751941 0.10336471 0.08692792
  0.1038629  0.09497348 0.11071908 0.09170929]
 [0.098

...

INFO:tensorflow:global_step/sec: 5.18054
INFO:tensorflow:probabilities = [[0.00002434 0.9856595  0.00021351 0.00015713 0.00038364 0.00000297
  0.00010765 0.00016749 0.01326315 0.0000208 ]
 [0.00000025 0.00000006 0.00000014 0.00019418 0.00000001 0.9996798
  0.0000002  0.00000002 0.0001152  0.00001013]
 [0.00000291 0.9976667  0.00008188 0.0006636  0.00064114 0.00001495
  0.00008027 0.00036872 0.00041878 0.00006112]
 [0.9983664  0.00000775 0.00034303 0.00019637 0.00000009 0.00024735
  0.0000301  0.0001749  0.00003407 0.00059999]
 [0.891894   0.00000375 0.00030662 0.00010663 0.00023602 0.0011121
  0.10568921 0.00000462 0.00060439 0.00004264]
 [0.00736531 0.00009824 0.00078939 0.00251225 0.00003286 0.97674316
  0.00039063 0.00707087 0.00452532 0.00047199]
 [0.0000456  0.00000147 0.00029159 0.00000091 0.00000703 0.00011168
  0.9995173  0.00000001 0.00002439 0.00000001]
 [0.00000193 0.00002344 0.00003394 0.04986431 0.00001106 0.9108039
  0.00003241 0.00000358 0.03465981 0.00456556]
 [0.000000

INFO:tensorflow:loss = 0.095368825, step = 19901 (19.304 sec)
INFO:tensorflow:probabilities = [[0.00000006 0.00000028 0.00018251 0.00034827 0.00000076 0.00000001
  0.         0.9993304  0.00010964 0.00002817]
 [0.00000774 0.9972203  0.00007454 0.00104704 0.00001153 0.00008695
  0.00003489 0.00045245 0.00101509 0.00004959]
 [0.00000969 0.9947332  0.00026206 0.00005319 0.0000345  0.00002327
  0.00302166 0.00021263 0.00163236 0.00001733]
 [0.00000749 0.00000037 0.00002363 0.00000024 0.999816   0.00003247
  0.00004203 0.00000156 0.00000733 0.00006904]
 [0.00000001 0.0000114  0.9981092  0.00003576 0.00002303 0.00000682
  0.00008583 0.00172106 0.0000063  0.00000048]
 [0.0000233  0.00000002 0.00064062 0.0000254  0.00000007 0.00000458
  0.00000019 0.00000028 0.9992887  0.00001674]
 [0.00031359 0.00181542 0.00052624 0.86146307 0.00000041 0.1356392
  0.00020674 0.0000001  0.00002431 0.0000109 ]
 [0.00000637 0.00000135 0.00000199 0.00014083 0.00017618 0.9799826
  0.00000567 0.00000775 0.0196508  

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.21878727.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2019-08-20T16:48:37Z
INFO:tensorflow:Graph was finalized.
Instructions for updating:
Use standard file APIs to check for files with this prefix.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model\model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2019-08-20-16:48:42
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9669, global_step = 20000, loss = 0.10676699
INFO:tensorflow:Saving 'checkpoint_path' summary for global step 20000: /tmp/mnist_convnet_model\model.ckpt-20000
{'accuracy': 0.9669, 'loss': 0.10676699, 'global_step': 20000}


SystemExit: 

c:\users\vernyjmo\appdata\local\continuum\miniconda3\lib\site-packages\IPython\core\interactiveshell.py:3304: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
